In [10]:
library(rhdf5)
library(edgeR)
library(MAST)
library(splatter)
library(DESeq2)
library(limma)
library(statmod)

Loading required package: limma
Loading required package: SummarizedExperiment
Loading required package: GenomicRanges
Loading required package: stats4
Loading required package: BiocGenerics
Loading required package: parallel

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:parallel’:

    clusterApply, clusterApplyLB, clusterCall, clusterEvalQ,
    clusterExport, clusterMap, parApply, parCapply, parLapply,
    parLapplyLB, parRapply, parSapply, parSapplyLB

The following object is masked from ‘package:limma’:

    plotMA

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, append, as.data.frame, cbind, colMeans, colnames,
    colSums, do.call, duplicated, eval, evalq, Filter, Find, get, grep,
    grepl, intersect, is.unsorted, lapply, lengths, Map, mapply, match,
    mget, order, paste, pmax, pmax.int, pmin, pmin.int, Position, rank,
    rbind, 

In [4]:
splat_simulate = function(input_rda, facLoc=1, facScale=0.3, deProb=0.1, dropoutPresent=FALSE, groupProb, batch_cells)
{
   # Estimate parameters from the data (it takes time, could be moved out of the function)
    # loads the params object from the rda
    load(input_rda)
    params = setParam(params, "group.prob", groupProb)
    params = setParam(params, "de.facScale", facScale)
    params = setParam(params, "de.prob", deProb)
    params = setParam(params, "de.facLoc", facLoc)
    params = setParam(params, "dropout.present", dropoutPresent)
    params = setParam(params, "batchCells", batch_cells)
    print(params)
    sg = splatSimulateGroups(param=params, verbose=TRUE)
    return (sg)
}

In [5]:
input_rda = '../hdf5_data/melanomaS2_estimated.rda'

In [6]:
simulate_groups = function(group_prob=c(0.5,0.5), loc_factor=2.5, scale_factor=0.3, batch_cells=50)
{
    group_prob = group_prob
    dropout_present = TRUE
    loc_factor = loc_factor
    scale_factor = scale_factor
    de_prob = 0.05
    batch_cells = 50
    sg = splat_simulate(input_rda = input_rda, groupProb = group_prob, dropoutPresent=dropout_present, facLoc = loc_factor, facScale= scale_factor, deProb=de_prob, batch_cells = batch_cells)

    data = assays(sg)$counts
    # remove genes that aren't expressed in at least 6 cells
    gkeep <- rowSums(data > 0) > 3;
    counts <- assays(sg)$counts[gkeep,]

    de_genes_mask = (rowData(sg)$DEFacGroup1[gkeep] != 1) & (rowData(sg)$DEFacGroup2[gkeep] == 1) | (rowData(sg)$DEFacGroup1[gkeep] == 1) & (rowData(sg)$DEFacGroup2[gkeep] != 1)

    marker_genes = rownames(sg)[gkeep][de_genes_mask]
    non_marker_genes = rownames(sg)[gkeep][!de_genes_mask]

    groups = colData(sg)$Group

    CPM = edgeR::cpm(counts)
    L <- list(count = counts, condt = groups, cpm=CPM)

    return (L)
}

In [9]:
loc2.5_eq = simulate_groups(group_prob=c(0.5,0.5), loc_factor=2.5, scale_factor=0.3, batch_cells=50)

ERROR: Error in setParam(params, "group.prob", groupProb): could not find function "setParam"


## Comparisons

In [26]:
edger_res = run_edgeRQLFDetRate(L)
edger_rlrt_res = run_edgeRLRT(L)
ttest_res = run_ttest(L)
wilcoxon_res = run_Wilcoxon(L)
limma_res = run_limmatrend(L)
voom_limma_res = run_voomlimma(L)
zinger_res = run_zingeR(L)

edgeRQLFDetRate


zingeR
Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial glm!”Warning message in eval(family$initialize):
“non-integer counts in a binomial gl

In [307]:
sum(is.na(ttest_res$df$pval))

[1] 10926

In [86]:
edger_perf = DE_Quality_AUC(edger_res$df,  marker_genes, non_marker_genes)
edger_rlrt_perf = DE_Quality_AUC(edger_rlrt_res$df, marker_genes, non_marker_genes)

ttest_perf = DE_Quality_AUC(ttest_res$df, marker_genes, non_marker_genes)
wilcoxon_perf = DE_Quality_AUC(wilcoxon_res$df, marker_genes, non_marker_genes)

limma_perf = DE_Quality_AUC(limma_res$df, marker_genes, non_marker_genes)
voom_limma_perf = DE_Quality_AUC(voom_limma_res$df, marker_genes, non_marker_genes)

zinger_perf = DE_Quality_AUC(zinger_res$df, marker_genes, non_marker_genes)

In [87]:
auc_results = setNames(as.list(c(edger_perf,edger_rlrt_perf, ttest_perf, wilcoxon_perf, limma_perf, voom_limma_perf, zinger_perf)), c("edger_qlf", "edger_rlrt", "ttest","wilcoxon", "limma", "voom_limma", "zinger"))

In [89]:
auc_results

$edger_qlf
[1] 0.9346349

$edger_rlrt
[1] 0.9378118

$ttest
[1] 0.9426624

$wilcoxon
[1] 0.9407307

$limma
[1] 0.9358031

$voom_limma
[1] 0.909893

$zinger
[1] 0.9383538

## Methods

In [91]:
DE_Quality_AUC <- function(p_vals_df, marker_genes, non_marker_genes) {
    res = p_vals_df
    p_vals = res$pval
    p_adj = p.adjust(p_vals, method = "BH")
    names_pVals = rownames(res)
    pVals <- p_vals[names_pVals %in% marker_genes | 
                   names_pVals %in% non_marker_genes]
    truth <- rep(1, times = length(pVals));
    truth[names_pVals %in% marker_genes] = 0;
    pred <- ROCR::prediction(pVals, truth)
    perf <- ROCR::performance(pred, "tpr", "fpr")
    # return(perf)
    aucObj <- ROCR::performance(pred, "auc")
    return(aucObj@y.values[[1]])
}


suppressPackageStartupMessages(library(SummarizedExperiment))
suppressPackageStartupMessages(library(scran))
suppressPackageStartupMessages(library(scDD))

run_scDD <- function(L) {
  message("scDD")
  session_info <- sessionInfo()
  tryCatch({
    timing <- system.time({
      scDatList <- list()
      (groups <- unique(L$condt))
      for (i in 1:length(groups)) {
        scDatList[[paste0("G", i)]] <- as.matrix(L$count[, which(L$condt == groups[i])])
      }
      datNorm.scran <- scDD::preprocess(scDatList, 
                                        ConditionNames = names(scDatList),
                                        zero.thresh = 1, median_norm = TRUE)
      condition <- L$condt[colnames(datNorm.scran)]
      condition <- as.numeric(as.factor(condition))
      names(condition) <- colnames(datNorm.scran)
      
      SDSumExp <- SummarizedExperiment(assays = list("NormCounts" = datNorm.scran),
                                       colData = data.frame(condition))
      prior_param <- list(alpha = 0.01, mu0 = 0, s0 = 0.01, a0 = 0.01, b0 = 0.01)
      scd <- scDD(SDSumExp, prior_param = prior_param, testZeroes = FALSE,
                  param = BiocParallel::MulticoreParam(workers = 1), 
                  condition = "condition", min.size = 3, min.nonzero = NULL)
      res <- results(scd)
    })
    
    hist(res$nonzero.pvalue, 50)
    hist(res$nonzero.pvalue.adj, 50)
    
    list(session_info = session_info,
         timing = timing,
         res = res,
         df = data.frame(pval = res$nonzero.pvalue,
                         padj = res$nonzero.pvalue.adj,
                         row.names = rownames(res)))
  }, error = function(e) {
    "scDD results could not be calculated"
    list(error=e, session_info = session_info)
  })
}



suppressPackageStartupMessages(library(MAST))
run_MASTtpmDetRate <- function(L) {
  message("MAST, TPM (including detection rate)")
  session_info <- sessionInfo()
  tryCatch({
    timing <- system.time({
      stopifnot(all(names(L$condt) == colnames(L$tpm)))
      grp <- L$condt
      cdr <- scale(colMeans(L$tpm > 0))
      sca <- FromMatrix(exprsArray = log2(L$tpm + 1), 
                        cData = data.frame(wellKey = names(grp), 
                                           grp = grp, cdr = cdr))
      zlmdata <- zlm.SingleCellAssay(~cdr + grp, sca)
      mast <- lrTest(zlmdata, "grp")
    })
    
    hist(mast[, "hurdle", "Pr(>Chisq)"], 50)
    
    list(session_info = session_info,
         timing = timing,
         res = mast,
         df = data.frame(pval = mast[, "hurdle", "Pr(>Chisq)"],
                         row.names = names(mast[, "hurdle", "Pr(>Chisq)"])))
  }, error = function(e) {
    "MASTtpmDetRate results could not be calculated"
    list(error=e, session_info = session_info)
  })
}

In [82]:

suppressPackageStartupMessages(library(edgeR))




run_edgeRQLFDetRate <- function(L) {
  message("edgeRQLFDetRate")
  session_info <- sessionInfo()
  tryCatch({
    timing <- system.time({
      dge <- DGEList(L$count, group = L$condt)
      dge <- calcNormFactors(dge)
      cdr <- scale(colMeans(L$count > 0))
      design <- model.matrix(~ cdr + L$condt)
      dge <- estimateDisp(dge, design = design)
      fit <- glmQLFit(dge, design = design)
      qlf <- glmQLFTest(fit)
      tt <- topTags(qlf, n = Inf)
    })
    
   # plotBCV(dge)
   # plotQLDisp(fit)
   # hist(tt$table$PValue, 50)
   # hist(tt$table$FDR, 50)
   # limma::plotMDS(dge, col = as.numeric(as.factor(L$condt)), pch = 19)
   # plotSmear(qlf)
    
    return (list(session_info = session_info,
         timing = timing,
         tt = tt,
         df = data.frame(pval = tt$table$PValue,
                         padj = tt$table$FDR,
                         row.names = rownames(tt$table))))
  }, error = function(e) {
    "edgeRQLFDetRate results could not be calculated"
    list(session_info = session_info)
  })
}

run_ttest <- function(L) {
  message("t-test")
  session_info <- sessionInfo()
  timing <- system.time({
    tmm <- edgeR::calcNormFactors(L$tpm)
    tpmtmm <- edgeR::cpm(L$tpm, lib.size = tmm * colSums(L$tpm))
    logtpm <- log2(tpmtmm + 1)
    idx <- seq_len(nrow(logtpm))
    names(idx) <- rownames(logtpm)
    ttest_p <- sapply(idx, function(i) {
      t.test(logtpm[i, ] ~ L$condt)$p.value
    })
})
  
  #hist(ttest_p, 50)
  
  list(session_info = session_info,
       timing = timing,
       df = data.frame(pval = ttest_p,
                       row.names = names(ttest_p)))
}

run_Wilcoxon <- function(L) {
  message("Wilcoxon")
  session_info <- sessionInfo()
  timing <- system.time({
    tmm <- edgeR::calcNormFactors(L$tpm)
    tpmtmm <- edgeR::cpm(L$tpm, lib.size = tmm * colSums(L$tpm))
    idx <- 1:nrow(tpmtmm)
    names(idx) <- rownames(tpmtmm)
    wilcox_p <- sapply(idx, function(i) {
      wilcox.test(tpmtmm[i, ] ~ L$condt)$p.value
    })
  })
  
  #hist(wilcox_p, 50)
  
  list(session_info = session_info,
       timing = timing,
       df = data.frame(pval = wilcox_p,
                       row.names = names(wilcox_p)))
}

run_limmatrend <- function(L) {
  message("limmatrend")
  session_info <- sessionInfo()
  timing <- system.time({
    dge <- DGEList(L$count, group = L$condt)
    dge <- calcNormFactors(dge)
    design <- model.matrix(~L$condt)
    y <- new("EList")
    y$E <- edgeR::cpm(dge, log = TRUE, prior.count = 3)
    fit <- lmFit(y, design = design)
    fit <- eBayes(fit, trend = TRUE, robust = TRUE)
    tt <- topTable(fit, n = Inf, adjust.method = "BH")
  })
  
  #hist(tt$P.Value, 50)
  #hist(tt$adj.P.Val, 50)
  #limma::plotMDS(dge, col = as.numeric(as.factor(L$condt)), pch = 19)
  #plotMD(fit)
  
  list(session_info = session_info,
       timing = timing,
       tt = tt,
       df = data.frame(pval = tt$P.Value,
                       padj = tt$adj.P.Val,
                       row.names = rownames(tt)))
}


suppressPackageStartupMessages(library(limma))
suppressPackageStartupMessages(library(edgeR))

run_voomlimma <- function(L) {
  message("voomlimma")
  session_info <- sessionInfo()
  timing <- system.time({
    dge <- DGEList(L$count, group = L$condt)
    dge <- calcNormFactors(dge)
    design <- model.matrix(~L$condt)
    vm <- voom(dge, design = design, plot = TRUE)
    fit <- lmFit(vm, design = design)
    fit <- eBayes(fit)
    tt <- topTable(fit, n = Inf, adjust.method = "BH")
  })
  
  #hist(tt$P.Value, 50)
  #hist(tt$adj.P.Val, 50)
  #limma::plotMDS(dge, col = as.numeric(as.factor(L$condt)), pch = 19)
  #plotMD(fit)
  
  list(session_info = session_info,
       timing = timing,
       tt = tt,
       df = data.frame(pval = tt$P.Value,
                       padj = tt$adj.P.Val,
                       row.names = rownames(tt)))
}

run_DESeq2 <- function(L) {
  message("DESeq2")
  session_info <- sessionInfo()
  tryCatch({
    timing <- system.time({
      cds <- newCountDataSet(FilteredData, conds)
      # DESeq normaliztion:

      cds <- estimateSizeFactors (cds)
      print (sizeFactors(cds))
      print (head(counts(cds, normalized = TRUE)))

      # Variance estimation:

      cds <- estimateDispersions (cds)

      print(str(fitInfo(cds)))
        
      dds <- DESeq(cds)
      res <- results(dds, contrast = c("condition", levels(factor(L$condt))[1], 
                                       levels(factor(L$condt))[2]), alpha = 0.05)
    })
    
    #plotDispEsts(dds)
    #plotMA(res)
    #summary(res)
    
    list(session_info = session_info,
         timing = timing,
         res = res,
         df = data.frame(pval = res$pval,
                         padj = res$padj,
                         row.names = rownames(res)))
  }, error = function(e) {
    "DESeq2 results could not be calculated"
    list(session_info = session_info, error=e)
  })
}

run_edgeRLRT <- function(L) {
  message("edgeRLRT")
  session_info <- sessionInfo()
  timing <- system.time({
    dge <- DGEList(L$count, group = L$condt)
    dge <- calcNormFactors(dge)
    design <- model.matrix(~L$condt)
    dge <- estimateDisp(dge, design = design)
    fit <- glmFit(dge, design = design)
    lrt <- glmLRT(fit)
    tt <- topTags(lrt, n = Inf)
  })
  
  #plotBCV(dge)
  #hist(tt$table$PValue, 50)
  #hist(tt$table$FDR, 50)
  #limma::plotMDS(dge, col = as.numeric(as.factor(L$condt)), pch = 19)
  #plotSmear(lrt)

  list(session_info = session_info,
       timing = timing,
       tt = tt,
       df = data.frame(pval = tt$table$PValue,
                       padj = tt$table$FDR,
                       row.names = rownames(tt$table)))
}


suppressPackageStartupMessages(library(edgeR))
suppressPackageStartupMessages(library(genefilter)) #for filtering functions

run_zingeR <- function(L) {
  message("zingeR")
  session_info <- sessionInfo()
  timing <- system.time({
    dge <- DGEList(L$count, group = L$condt)
    dge <- calcNormFactors(dge)
    design <- model.matrix(~L$condt)
    niter <- 30 #you may want to increase this for large (~ >200 cells) datasets, can checked this by looking whether the weight distribution of zero counts is still changing over the last few iterations.
    zeroWeights <- zeroWeightsLibSizeFast(dge, design, plot = FALSE, 
                                          maxit = niter, initialWeightAt0 = TRUE, 
                                          plotW = FALSE)
    dge$weights <- zeroWeights
    dge <- estimateDispWeighted(dge, design, weights = dge$weights)
    fit <- glmFit(dge, design = design)
    fit$df.residual <- rowSums(fit$weights) - ncol(design)
    lrt <- glmLRTOld(fit, test = "F")
    ## independent filtering from DESeq2
    pval <- lrt$table$PValue
    baseMean <- unname(rowMeans(sweep(dge$counts, 2, dge$samples$norm.factors, FUN = "*")))
    hlp <- pvalueAdjustment_kvdb(baseMean = baseMean, pValue = pval)
    padj <- hlp$padj
    tt <- topTags(lrt, n = Inf)    
  })
  
  #plotBCV(dge)
  #hist(tt$table$PValue, 50)
  #hist(tt$table$FDR, 50)
  #limma::plotMDS(dge, col = as.numeric(as.factor(L$condt)), pch = 19)
  #plotSmear(lrt)
  #weights for zero counts to check if zero-inflation was identified
  #hist(zeroWeights[dge$counts == 0], xlab = "weight", 
   #    main = "post. prob. on zero-inflation for zero counts") 

  list(session_info = session_info,
       timing = timing,
       tt = tt, #this does however not contain the good adjusted p-values, these ar in padj
       df = data.frame(pval = lrt$table$PValue,
                       padj = padj,
                       row.names = rownames(lrt)))
}


### extra functions you will need 'in order of appearance'
### EM-algorithm for estimating weights
zeroWeightsLibSizeFast <- function(counts, design, initialWeightAt0 = TRUE, 
                                   maxit = 100, plot = FALSE, plotW = FALSE, 
                                   designZI = NULL, wTol = 1e-4){
    require(edgeR)
    if(plot | plotW) par(mfrow=c(1,plot+plotW))    
    counts <- DGEList(counts)
    counts <- calcNormFactors(counts)
    effLibSize <- counts$samples$lib.size*counts$samples$norm.factors
    logEffLibSize <- log(effLibSize)
    zeroId <- counts$counts==0
    w <- matrix(1,nrow=nrow(counts),ncol=ncol(counts), dimnames=list(c(1:nrow(counts)), NULL))
    #if(initialWeightAt0) w[zeroId] <- 0.1 else w[zeroId] <- 0.9
      ## starting values based on P(zero) in the library
    for(k in 1:ncol(w)) w[counts$counts[,k]==0,k] <- 1-mean(counts$counts[,k]==0)
    
    for(i in 1:maxit){
	counts$weights <- w
	
	### M-step counts
	counts <- estimateGLMCommonDisp(counts, design, interval=c(0,10))
	counts <- estimateGLMTagwiseDisp(counts, design, prior.df=0, min.row.sum=1)
	if(plot) plotBCV(counts)
	fit <- glmFit(counts, design)
	likC <- dnbinom(counts$counts, mu=fit$fitted.values, size=1/counts$tagwise.dispersion)
	
	### M-step mixture parameter: model zero probability
	successes <- colSums(1-w) #P(zero)
	failures <- colSums(w) #1-P(zero)
	if(is.null(designZI)){
	zeroFit <- glm(cbind(successes,failures) ~ logEffLibSize, family="binomial")} else{
	zeroFit <- glm(cbind(successes,failures) ~-1+designZI, family="binomial")}
	pi0Hat <- predict(zeroFit,type="response") 
	
	## E-step: Given estimated parameters, calculate expected value of weights
	pi0HatMat <- expandAsMatrix(pi0Hat,dim=dim(counts),byrow=TRUE)
	wOld <- w
	w <- 1-pi0HatMat*zeroId/(pi0HatMat*zeroId+(1-pi0HatMat)*likC*zeroId+1e-15)
	rownames(w) <- rownames(wOld)
	if(plotW) hist(w[zeroId])
    }
    return(w)
}


### estimateDispWeighted function and related functions
.comboGroups <- function(truths) 
# Function that returns a list of vectors of indices,
# where each vector refers to the rows with the same
# combination of TRUE/FALSE values in 'truths'.
# 
# written by Aaron Lun
# Created 24 October 2014
{
#	Integer packing will only work for 31 libraries at a time.	
	assembly <- list()
	collected <- 0L
	step <- 31L
	bits <- as.integer(2^(1:step-1L))

	while (collected < ncol(truths)) {
		upper <- pmin(ncol(truths) - collected, step)
		keys <- t(truths[,collected+1:upper,drop=FALSE]) * bits[1:upper]
		assembly[[length(assembly)+1L]] <- as.integer(colSums(keys))
		collected <- collected + step
	}

#	Figuring out the unique components.
	o <- do.call(order, assembly)
	nr <- nrow(truths)
	is.different <- logical(nr)
	for (i in 1:length(assembly)) { 
		is.different <- is.different | c(TRUE, diff(assembly[[i]][o])!=0L)
	}
	first.of.each <- which(is.different)
	last.of.each <- c(first.of.each[-1]-1L, nr)

#	Returning the groups.
	output <- list()
	for (u in 1:length(first.of.each)) {
		output[[u]] <- o[first.of.each[u]:last.of.each[u]]
	}
	return(output)
}



.residDF <- function(zero, design)
#	Effective residual degrees of freedom after adjusting for exact zeros
#	Gordon Smyth and Aaron Lun
#	Created 6 Jan 2014.  Last modified 2 Sep 2014
{
	nlib <- ncol(zero)
	ncoef <- ncol(design)
	nzero <- as.integer(rowSums(zero))

#	Default is no zero
	DF <- rep(nlib-ncoef,length(nzero))

#	All zero case
	DF[nzero==nlib] <- 0L

#	Anything in between?
	somezero <- nzero>0L & nzero<nlib
	if(any(somezero)) {
		zero2 <- zero[somezero,,drop=FALSE]
		groupings <- .comboGroups(zero2)

#		Identifying the true residual d.f. for each of these rows.			
		DF2 <- nlib-nzero[somezero]
		for (u in 1:length(groupings)) {
			i <- groupings[[u]]
			zeroi <- zero2[i[1],]
			DF2[i] <- DF2[i]-qr(design[!zeroi,,drop=FALSE])$rank
		}
		DF2 <- pmax(DF2, 0L)
		DF[somezero] <- DF2
	}

	DF
}



estimateDispWeighted = function (y, design = NULL, prior.df = NULL, trend.method = "locfit", tagwise = TRUE, span = NULL, min.row.sum = 5, grid.length = 21, 
    grid.range = c(-10, 10), robust = FALSE, winsor.tail.p = c(0.05, 
        0.1), tol = 1e-06, weights=NULL) 
{
    #adjusted by Koen VdB on 04 March 2016
    if (!is(y, "DGEList")) 
        stop("y must be a DGEList")
    trend.method <- match.arg(trend.method, c("none", "loess", 
        "locfit", "movingave"))
    ntags <- nrow(y$counts)
    nlibs <- ncol(y$counts)
    offset <- getOffset(y)
    AveLogCPM <- aveLogCPM(y)
    offset <- expandAsMatrix(offset, dim(y))
    sel <- rowSums(y$counts) >= min.row.sum
    spline.pts <- seq(from = grid.range[1], to = grid.range[2], 
        length = grid.length)
    spline.disp <- 0.1 * 2^spline.pts
    grid.vals <- spline.disp/(1 + spline.disp)
    l0 <- matrix(0, sum(sel), grid.length)
    if (is.null(design)) {
        cat("Design matrix not provided. Switch to the classic mode.\n")
        group <- y$samples$group <- as.factor(y$samples$group)
        if (length(levels(group)) == 1) 
            design <- matrix(1, nlibs, 1)
        else design <- model.matrix(~group)
        if (all(tabulate(group) <= 1)) {
            warning("There is no replication, setting dispersion to NA.")
            y$common.dispersion <- NA
            return(y)
        }
        pseudo.obj <- y[sel, ]
        q2q.out <- equalizeLibSizes(y[sel, ], dispersion = 0.01)
        pseudo.obj$counts <- q2q.out$pseudo
        ysplit <- splitIntoGroups(pseudo.obj)
        delta <- optimize(commonCondLogLikDerDelta, interval = c(1e-04, 
            100/(100 + 1)), tol = tol, maximum = TRUE, y = ysplit, 
            der = 0)
        delta <- delta$maximum
        disp <- delta/(1 - delta)
        q2q.out <- equalizeLibSizes(y[sel, ], dispersion = disp)
        pseudo.obj$counts <- q2q.out$pseudo
        ysplit <- splitIntoGroups(pseudo.obj)
        for (j in 1:grid.length) for (i in 1:length(ysplit)) l0[, 
            j] <- condLogLikDerDelta(ysplit[[i]], grid.vals[j], 
            der = 0) + l0[, j]
    }
    else {
        design <- as.matrix(design)
        if (ncol(design) >= ncol(y$counts)) {
            warning("No residual df: setting dispersion to NA")
            y$common.dispersion <- NA
            return(y)
        }
        glmfit <- glmFit(y$counts[sel, ], design, offset = offset[sel, 
            ], dispersion = 0.05, prior.count = 0, weights=weights[sel,]) ###www 
        zerofit <- (glmfit$fitted.values < 1e-04) & (glmfit$counts < 
            1e-04)
        by.group <- .comboGroups(zerofit)
        for (subg in by.group) {
            cur.nzero <- !zerofit[subg[1], ]
            if (!any(cur.nzero)) {
                next
            }
            if (all(cur.nzero)) {
                redesign <- design
            }
            else {
                redesign <- design[cur.nzero, , drop = FALSE]
                QR <- qr(redesign)
                redesign <- redesign[, QR$pivot[1:QR$rank], drop = FALSE]
                if (nrow(redesign) == ncol(redesign)) {
                  next
                }
            }
            last.beta <- NULL
            for (i in 1:grid.length) {
                out <- adjustedProfileLik(spline.disp[i], y = y$counts[sel, 
                  ][subg, cur.nzero, drop = FALSE], design = redesign, 
                  offset = offset[sel, ][subg, cur.nzero, drop = FALSE], 
                  start = last.beta, get.coef = TRUE, weights=weights[sel,][subg, cur.nzero, drop = FALSE]) ###www
                l0[subg, i] <- out$apl
                last.beta <- out$beta
            }
        }
    }
    out.1 <- WLEB(theta = spline.pts, loglik = l0, covariate = AveLogCPM[sel], 
        trend.method = trend.method, span = span, individual = FALSE, 
        m0.out = TRUE)
    y$common.dispersion <- 0.1 * 2^out.1$overall
    disp.trend <- 0.1 * 2^out.1$trend
    y$trended.dispersion <- rep(disp.trend[which.min(AveLogCPM[sel])], 
        ntags)
    y$trended.dispersion[sel] <- disp.trend
    y$trend.method <- trend.method
    y$AveLogCPM <- AveLogCPM
    y$span <- out.1$span
    if (!tagwise) 
        return(y)
    if (is.null(prior.df)) {
        glmfit <- glmFit(y$counts[sel, ], design, offset = offset[sel, 
            ], dispersion = disp.trend, prior.count = 0, weights=weights[sel,]) ###www
        df.residual <- glmfit$df.residual
        zerofit <- (glmfit$fitted.values < 1e-04) & (glmfit$counts < 
            1e-04)
        df.residual <- .residDF(zerofit, design)
        s2 <- glmfit$deviance/df.residual
        s2[df.residual == 0] <- 0
        s2 <- pmax(s2, 0)
        s2.fit <- squeezeVar(s2, df = df.residual, covariate = AveLogCPM[sel], 
            robust = robust, winsor.tail.p = winsor.tail.p)
        prior.df <- s2.fit$df.prior
    }
    ncoefs <- ncol(design)
    prior.n <- prior.df/(nlibs - ncoefs)
    if (trend.method != "none") {
        y$tagwise.dispersion <- y$trended.dispersion
    }
    else {
        y$tagwise.dispersion <- rep(y$common.dispersion, ntags)
    }
    too.large <- prior.n > 1e+06
    if (!all(too.large)) {
        temp.n <- prior.n
        if (any(too.large)) {
            temp.n[too.large] <- 1e+06
        }
        out.2 <- WLEB(theta = spline.pts, loglik = l0, prior.n = temp.n, 
            covariate = AveLogCPM[sel], trend.method = trend.method, 
            span = span, overall = FALSE, trend = FALSE, m0 = out.1$shared.loglik)
        if (!robust) {
            y$tagwise.dispersion[sel] <- 0.1 * 2^out.2$individual
        }
        else {
            y$tagwise.dispersion[sel][!too.large] <- 0.1 * 2^out.2$individual[!too.large]
        }
    }
    if (!robust) {
        y$prior.df <- prior.df
        y$prior.n <- prior.n
    }
    else {
        y$prior.df <- y$prior.n <- rep(Inf, ntags)
        y$prior.df[sel] <- prior.df
        y$prior.n[sel] <- prior.n
    }
    y
}


### old glmLRT function for F-test
glmLRTOld <- function(glmfit,coef=ncol(glmfit$design),contrast=NULL,test="chisq")
#	Tagwise likelihood ratio tests for DGEGLM
#	Gordon Smyth, Davis McCarthy and Yunshun Chen.
#	Created 1 July 2010.  Last modified 22 Nov 2013.
{
#	Check glmfit
	if(!is(glmfit,"DGEGLM")) {
		if(is(glmfit,"DGEList") && is(coef,"DGEGLM")) {
			stop("First argument is no longer required. Rerun with just the glmfit and coef/contrast arguments.")
		}
		stop("glmfit must be an DGEGLM object (usually produced by glmFit).")
	}
	if(is.null(glmfit$AveLogCPM)) glmfit$AveLogCPM <- aveLogCPM(glmfit)
	nlibs <- ncol(glmfit)

#	Check test
	test <- match.arg(test,c("F","f","chisq"))
	if(test=="f") test <- "F"
	
#	Check design matrix
	design <- as.matrix(glmfit$design)
	nbeta <- ncol(design)
	if(nbeta < 2) stop("Need at least two columns for design, usually the first is the intercept column")
	coef.names <- colnames(design)

#	Evaluate logFC for coef to be tested
#	Note that contrast takes precedence over coef: if contrast is given
#	then reform design matrix so that contrast of interest is last column.
	if(is.null(contrast)) {
		if(length(coef) > 1) coef <- unique(coef)
		if(is.character(coef)) {
			check.coef <- coef %in% colnames(design)
			if(any(!check.coef)) stop("One or more named coef arguments do not match a column of the design matrix.")
			coef.name <- coef
			coef <- match(coef, colnames(design))
		}
		else
			coef.name <- coef.names[coef]
		logFC <- glmfit$coefficients[,coef,drop=FALSE]/log(2)
	} else {
		contrast <- as.matrix(contrast)
		qrc <- qr(contrast)
		ncontrasts <- qrc$rank
		if(ncontrasts==0) stop("contrasts are all zero")
		coef <- 1:ncontrasts
		if(ncontrasts < ncol(contrast)) contrast <- contrast[,qrc$pivot[coef]]
		logFC <- drop((glmfit$coefficients %*% contrast)/log(2))
		if(ncontrasts>1) {
			coef.name <- paste("LR test of",ncontrasts,"contrasts")
		} else {
			contrast <- drop(contrast)
			i <- contrast!=0
			coef.name <- paste(paste(contrast[i],coef.names[i],sep="*"),collapse=" ")
		}
		Dvec <- rep.int(1,nlibs)
		Dvec[coef] <- diag(qrc$qr)[coef]
		Q <- qr.Q(qrc,complete=TRUE,Dvec=Dvec)
		design <- design %*% Q
	}
	if(length(coef)==1) logFC <- as.vector(logFC)

#	Null design matrix
	design0 <- design[,-coef,drop=FALSE]

#	Null fit
	fit.null <- glmFit(glmfit$counts,design=design0,offset=glmfit$offset,weights=glmfit$weights,dispersion=glmfit$dispersion,prior.count=0)

#	Likelihood ratio statistic
	LR <- fit.null$deviance - glmfit$deviance
	### ADDED
	fit.null$df.residual <- rowSums(fit.null$weights)-ncol(design0)
	## END ADDED
	df.test <- fit.null$df.residual - glmfit$df.residual ## okay

#	Chisquare or F-test	
	LRT.pvalue <- switch(test,
		"F" = {
			phi <- quantile(glmfit$dispersion,p=0.5)
			mu <- quantile(glmfit$fitted.values,p=0.5)
			gamma.prop <- (phi*mu/(1 + phi*mu))^2
			prior.df <- glmfit$prior.df
			if(is.null(prior.df)) prior.df <- 20
			glmfit$df.total <- glmfit$df.residual + prior.df/gamma.prop
			pf(LR/df.test, df1=df.test, df2=glmfit$df.total, lower.tail = FALSE, log.p = FALSE)
		},
		"chisq" = pchisq(LR, df=df.test, lower.tail = FALSE, log.p = FALSE)
	)

	rn <- rownames(glmfit)
	if(is.null(rn))
		rn <- 1:nrow(glmfit)
	else
		rn <- make.unique(rn)
	tab <- data.frame(
		logFC=logFC,
		logCPM=glmfit$AveLogCPM,
		LR=LR,
		PValue=LRT.pvalue,
		row.names=rn
	)
	glmfit$counts <- NULL
	glmfit$table <- tab 
	glmfit$comparison <- coef.name
	glmfit$df.test <- df.test
	new("DGELRT",unclass(glmfit))
}


### independent filtering from DESeq2, slightly adapted
pvalueAdjustment_kvdb <- function(baseMean, filter, pValue,
                             theta, alpha=0.05, pAdjustMethod="BH") {
  # perform independent filtering
    if (missing(filter)) {
      filter <- baseMean
    }
    if (missing(theta)) {
      lowerQuantile <- mean(filter == 0)
      if (lowerQuantile < .95) upperQuantile <- .95 else upperQuantile <- 1
      theta <- seq(lowerQuantile, upperQuantile, length=50)
    }

    # do filtering using genefilter
    stopifnot(length(theta) > 1)
    filtPadj <- filtered_p(filter=filter, test=pValue,
                           theta=theta, method=pAdjustMethod) 
    numRej  <- colSums(filtPadj < alpha, na.rm = TRUE)
    # prevent over-aggressive filtering when all genes are null,
    # by requiring the max number of rejections is above a fitted curve.
    # If the max number of rejection is not greater than 10, then don't
    # perform independent filtering at all.
    lo.fit <- lowess(numRej ~ theta, f=1/5)
    if (max(numRej) <= 10) {
      j <- 1
    } else { 
      residual <- if (all(numRej==0)) {
        0
      } else {
        numRej[numRej > 0] - lo.fit$y[numRej > 0]
      }
      thresh <- max(lo.fit$y) - sqrt(mean(residual^2))
      j <- if (any(numRej > thresh)) {
        which(numRej > thresh)[1]
      } else {
        1  
      }
    }
    padj <- filtPadj[, j, drop=TRUE]
    cutoffs <- quantile(filter, theta)
    filterThreshold <- cutoffs[j]
    filterNumRej <- data.frame(theta=theta, numRej=numRej)
    filterTheta <- theta[j]

    return(list(padj=padj, filterThreshold=filterThreshold, filterTheta=filterTheta, filterNumRej = filterNumRej, lo.fit=lo.fit, alpha=alpha))

}



In [38]:
# Library size normalization
lib_size = colSums(counts)
norm <- t(t(counts)/lib_size * median(lib_size)) 

In [55]:
norm

Cell1    Cell2    Cell3    Cell4    Cell5     Cell6     Cell7    
Gene1     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene2     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene3     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene4     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene5     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene6     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene7     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene8     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene9     1.265419 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene10    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene11    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene12    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene13    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene14    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene15    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene16    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene17    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene18    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene19    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene20    0.000000 0        0.000000 0.000000 0.0000000 0         4.740937 
Gene21    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene22    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene23    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene24    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene25    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene26    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene27    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene28    0.000000 0        0.000000 0.000000 0.9768035 0         0.000000 
Gene29    0.000000 0        2.256734 5.016424 0.0000000 0         1.777851 
Gene30    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
⋮         ⋮        ⋮        ⋮        ⋮        ⋮         ⋮         ⋮        
Gene19899 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19900 0.000000  0.00000 0        0        0.0000000 0.9242703 0.0000000
Gene19901 0.000000  0.00000 0        0        2.9304105 0.0000000 0.0000000
Gene19902 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19903 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19904 3.796256 16.57212 0        0        0.0000000 0.0000000 0.0000000
Gene19905 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19906 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19907 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19908 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19909 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19910 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19911 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19912 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19913 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19914 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19915 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19916 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19917 3.796256  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19918 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19919 0.000000  0.00000 0        0        0.0000000 0.

In [53]:
wc_res = run_wilcox(norm, L$condt)

Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

...

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot compute exact p-value with ties”Warning message in wilcox.test.default(x[group == "Group2"], x[group == "Group1"]):
“cannot 

In [54]:
wc_res

Gene1        Gene2        Gene3        Gene4        Gene5        Gene6 
1.287235e-01 1.079141e-01          NaN          NaN 3.773284e-01          NaN 
       Gene7        Gene8        Gene9       Gene10       Gene11       Gene12 
         NaN 2.967890e-01 1.287235e-01          NaN          NaN          NaN 
      Gene13       Gene14       Gene15       Gene16       Gene17       Gene18 
         NaN          NaN 3.773284e-01 9.087200e-01          NaN          NaN 
      Gene19       Gene20       Gene21       Gene22       Gene23       Gene24 
         NaN 3.308442e-02          NaN          NaN 3.773284e-01          NaN 
      Gene25       Gene26       Gene27       Gene28       Gene29       Gene30 
         NaN 9.087200e-01          NaN 6.363179e-01 4.981447e-04 7.648670e-01 
      Gene31       Gene32       Gene33       Gene34       Gene35       Gene36 
         NaN          NaN          NaN 2.424471e-03          NaN          NaN 
      Gene37       Gene38       Gene39       Gene40       Gene41       Gene42 
2.967890e-01          NaN          NaN 9.087200e-01          NaN 1.287235e-01 
      Gene43       Gene44       Gene45       Gene46       Gene47       Gene48 
         NaN          NaN          NaN          NaN          NaN 9.542850e-01 
      Gene49       Gene50       Gene51       Gene52       Gene53       Gene54 
         NaN          NaN          NaN 2.967890e-01          NaN          NaN 
      Gene55       Gene56       Gene57       Gene58       Gene59       Gene60 
6.650168e-02 8.092483e-01 3.591838e-02          NaN 5.079747e-01          NaN 
      Gene61       Gene62       Gene63       Gene64       Gene65       Gene66 
9.542850e-01          NaN 1.079006e-01          NaN          NaN          NaN 
      Gene67       Gene68       Gene69       Gene70       Gene71       Gene72 
         NaN          NaN          NaN 3.773284e-01 3.810057e-02          NaN 
      Gene73       Gene74       Gene75       Gene76       Gene77       Gene78 
2.623873e-01 1.287235e-01 3.773284e-01 5.856922e-02          NaN          NaN 
      Gene79       Gene80       Gene81       Gene82       Gene83       Gene84 
         NaN 9.087200e-01 4.018304e-03          NaN 1.287235e-01 1.287235e-01 
      Gene85       Gene86       Gene87       Gene88       Gene89       Gene90 
2.967890e-01 2.967890e-01          NaN 4.778528e-01          NaN 5.250512e-01 
      Gene91       Gene92       Gene93       Gene94       Gene95       Gene96 
         NaN 1.079006e-01 3.773284e-01 9.357998e-01 1.129918e-03          NaN 
      Gene97       Gene98       Gene99      Gene100      Gene101      Gene102 
         NaN 1.079006e-01 1.971033e-01 7.826395e-01 2.967890e-01 2.967890e-01 
     Gene103      Gene104      Gene105      Gene106      Gene107      Gene108 
5.856922e-02          NaN          NaN          NaN          NaN          NaN 
     Gene109      Gene110      Gene111      Gene112      Gene113      Gene114 
         NaN 9.087200e-01          NaN          NaN 8.517117e-01          NaN 
     Gene115      Gene116      Gene117      Gene118      Gene119      Gene120 
         NaN 7.052206e-01          NaN 2.967890e-01 1.287235e-01 1.475122e-01 
     Gene121      Gene122      Gene123      Gene124      Gene125      Gene126 
9.542850e-01          NaN          NaN          NaN          NaN          NaN 
     Gene127      Gene128      Gene129      Gene130      Gene131      Gene132 
5.682682e-03          NaN          NaN          NaN          NaN 3.773284e-01 
     Gene133      Gene134      Gene135      Gene136      Gene137      Gene138 
1.626542e-01          NaN 7.935460e-01          NaN 3.773284e-01 2.967890e-01 
     Gene139      Gene140      Gene141      Gene142      Gene143      Gene144 
         NaN 2.529012e-01 3.773284e-01          NaN          NaN 2.613253e-03 
     Gene145      Gene146      Gene147      Gene148      Gene149      Gene150 
1.079006e-01          NaN          NaN          NaN          NaN 6.363179e-01 
     Gene151      Gene152      Gene153      Gene154      

In [43]:
wt = wilcox.test(c(1,2,3),c(2,3,4))

Warning message in wilcox.test.default(c(1, 2, 3), c(2, 3, 4)):
“cannot compute exact p-value with ties”

In [51]:
run_wilcox = function(norm, group)
{
    pVals <- apply(
    norm, 1, function(x) {
        wilcox.test(
            x[group == 'Group2'], 
            x[group == 'Group1']
        )$p.value
    })
}

In [56]:
run_ttest = function(norm, group)
{
    pVals <- apply(
    norm, 1, function(x) {
        t.test(
            x[group == 'Group2'], 
            x[group == 'Group1']
        )$p.value
    })
}

In [58]:
tt_res = run_ttest(norm, L$condt)

In [59]:
tt_res

Gene1        Gene2        Gene3        Gene4        Gene5        Gene6 
2.399621e-01 1.295141e-01          NaN          NaN 3.265270e-01          NaN 
       Gene7        Gene8        Gene9       Gene10       Gene11       Gene12 
         NaN 3.281833e-01 1.914811e-01          NaN          NaN          NaN 
      Gene13       Gene14       Gene15       Gene16       Gene17       Gene18 
         NaN          NaN 3.265270e-01 4.385644e-01          NaN          NaN 
      Gene19       Gene20       Gene21       Gene22       Gene23       Gene24 
         NaN 5.783250e-02          NaN          NaN 3.265270e-01          NaN 
      Gene25       Gene26       Gene27       Gene28       Gene29       Gene30 
         NaN 6.164196e-01          NaN 5.285259e-01 2.845835e-03 6.502079e-01 
      Gene31       Gene32       Gene33       Gene34       Gene35       Gene36 
         NaN          NaN          NaN 3.903832e-02          NaN          NaN 
      Gene37       Gene38       Gene39       Gene40       Gene41       Gene42 
3.281833e-01          NaN          NaN 6.401802e-01          NaN 2.470343e-01 
      Gene43       Gene44       Gene45       Gene46       Gene47       Gene48 
         NaN          NaN          NaN          NaN          NaN 5.383385e-01 
      Gene49       Gene50       Gene51       Gene52       Gene53       Gene54 
         NaN          NaN          NaN 3.281833e-01          NaN          NaN 
      Gene55       Gene56       Gene57       Gene58       Gene59       Gene60 
1.184944e-01 6.011226e-01 2.123466e-01          NaN 8.735729e-01          NaN 
      Gene61       Gene62       Gene63       Gene64       Gene65       Gene66 
4.428890e-01          NaN 1.321647e-01          NaN          NaN          NaN 
      Gene67       Gene68       Gene69       Gene70       Gene71       Gene72 
         NaN          NaN          NaN 3.265270e-01 8.598778e-02          NaN 
      Gene73       Gene74       Gene75       Gene76       Gene77       Gene78 
1.778832e-01 1.645486e-01 3.265270e-01 1.270075e-01          NaN          NaN 
      Gene79       Gene80       Gene81       Gene82       Gene83       Gene84 
         NaN 6.413285e-01 1.538543e-02          NaN 1.692456e-01 2.245510e-01 
      Gene85       Gene86       Gene87       Gene88       Gene89       Gene90 
3.281833e-01 3.281833e-01          NaN 3.123188e-01          NaN 7.013335e-01 
      Gene91       Gene92       Gene93       Gene94       Gene95       Gene96 
         NaN 9.573419e-02 3.265270e-01 7.526387e-01 2.308893e-02          NaN 
      Gene97       Gene98       Gene99      Gene100      Gene101      Gene102 
         NaN 9.258016e-02 1.782539e-01 3.836297e-01 3.281833e-01 3.281833e-01 
     Gene103      Gene104      Gene105      Gene106      Gene107      Gene108 
1.623291e-01          NaN          NaN          NaN          NaN          NaN 
     Gene109      Gene110      Gene111      Gene112      Gene113      Gene114 
         NaN 4.673787e-01          NaN          NaN 6.583438e-01          NaN 
     Gene115      Gene116      Gene117      Gene118      Gene119      Gene120 
         NaN 4.396569e-01          NaN 3.281833e-01 1.621738e-01 3.409765e-01 
     Gene121      Gene122      Gene123      Gene124      Gene125      Gene126 
8.630565e-01          NaN          NaN          NaN          NaN          NaN 
     Gene127      Gene128      Gene129      Gene130      Gene131      Gene132 
1.470407e-02          NaN          NaN          NaN          NaN 3.265270e-01 
     Gene133      Gene134      Gene135      Gene136      Gene137      Gene138 
1.429634e-01          NaN 9.860310e-01          NaN 3.265270e-01 3.281833e-01 
     Gene139      Gene140      Gene141      Gene142      Gene143      Gene144 
         NaN 1.591236e-01 3.265270e-01          NaN          NaN 2.716630e-03 
     Gene145      Gene146      Gene147      Gene148      Gene149      Gene150 
1.943001e-01          NaN          NaN          NaN          NaN 2.446412e-01 
     Gene151      Gene152      Gene153      Gene154      

In [60]:
?t.test

In [74]:
all(norm[3,]==0)

[1] TRUE

In [61]:
norm

Cell1    Cell2    Cell3    Cell4    Cell5     Cell6     Cell7    
Gene1     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene2     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene3     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene4     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene5     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene6     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene7     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene8     0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene9     1.265419 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene10    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene11    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene12    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene13    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene14    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene15    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene16    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene17    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene18    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene19    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene20    0.000000 0        0.000000 0.000000 0.0000000 0         4.740937 
Gene21    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene22    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene23    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene24    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene25    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene26    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene27    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
Gene28    0.000000 0        0.000000 0.000000 0.9768035 0         0.000000 
Gene29    0.000000 0        2.256734 5.016424 0.0000000 0         1.777851 
Gene30    0.000000 0        0.000000 0.000000 0.0000000 0         0.000000 
⋮         ⋮        ⋮        ⋮        ⋮        ⋮         ⋮         ⋮        
Gene19899 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19900 0.000000  0.00000 0        0        0.0000000 0.9242703 0.0000000
Gene19901 0.000000  0.00000 0        0        2.9304105 0.0000000 0.0000000
Gene19902 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19903 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19904 3.796256 16.57212 0        0        0.0000000 0.0000000 0.0000000
Gene19905 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19906 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19907 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19908 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19909 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19910 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19911 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19912 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19913 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19914 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19915 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19916 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19917 3.796256  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19918 0.000000  0.00000 0        0        0.0000000 0.0000000 0.0000000
Gene19919 0.000000  0.00000 0        0        0.0000000 0.